# Workshop: scraping HTML data

### Monday March 28 and Wednesday March 30, 2022

In today's workshop we'll start on a more ambitious programming project than we have considered in previous weeks.
We will spend today's lecture and next writing code to examine parts of the network structure among Wikipedia pages.

Our main tool for the job will be <a href='https://beautiful-soup-4.readthedocs.io/en/latest/'>BeautifulSoup</a>

## Background: networks

Okay, first and foremost, what is a network?

We'll take a few minutes to talk about this and draw some pretty pictures on the board, or you can read the wikipedia page here: https://en.wikipedia.org/wiki/Complex_network

Today, we'll look at the network formed by the collection of all English-language Wikipedia pages.
In this network, the vertices correspond to Wikipedia pages, and an edge joins two pages for which one links to the other (we can discuss whether this relation should be binary or directed below).

In particular, we're going to consider the problem of finding the $k$-hop neighborhood of a wikipedia page.

We want to start at a page, and walk k hops from that page, and return a list of all the URLs of those pages.

So let's break the process into a few key steps:

1. Retrieve the HTML of the given URL.
2. Parse the HTML
3. Identify all the URLs in the HTML
4. Determine which URLs are links to other Wikipedia pages

We're going to write a function for each of these key steps, and then we'll put them all together to accomplish our task.

### First things first: grabbing a page.

First and foremost, we need a function that takes a Wikipedia URL and retrieves the HTML stored at that page.
Write a function `retrieve_html` that takes a string as its only argument and, treating that string as a URL, retrieves the HTML stored at that URL, and returns that HTML string.
You might like to include some error checking to make sure `s` is a string; in the event that the string is not a valid URL, you'll notice that `urllib` already raises an error for us.

In [13]:
def retrieve_html( s ):
    # CODE GOES HERE. Don't forget to remove pass.
    pass

### Step 2: Parsing HTML

This one we pretty much know how to do-- we saw this in the lecture videos; it's the whole reason we want to use `beautifulsoup`!

Write a function that takes an HTML string (i.e., produced by `response.read()`), and returns the `BeautifulSoup` parse of the HTML.

In [14]:
def parse_html( html_str ):
    # CODE GOES HERE. Don't forget to remove pass.
    pass

### Step 3: Extracting links

Now, the important step-- extracting the links from the page.

Write a function `extract_links` that takes a single `BeautifulSoup` object as its only argument and returns a list of `Tag` objects corresponding to all and only the `a` tags in the HTML file.
In a subsequent function, we will filter this list and keep only the links that point to other Wikipedia pages.

In [16]:
def extract_links( soup ):
    # CODE GOES HERE. Don't forget to remove pass.
    pass

### Step 4: Keeping Wikipedia links

Now we need to filter the list of links.
To do that, we need a function that takes an `a` tag object and returns a Boolean corresponding to whether or not it points to a Wikipedia page.

This is going to be a bit tricky-- not all links are links to Wikipedia, and not all Wikipedia links point to pages.

To see an example, let's look at this Wikipedia page: https://en.wikipedia.org/wiki/George_E._P._Box 

Looking at this page, we see that there are lots of links to other Wikipedia pages (e.g., the page for <a href='https://en.wikipedia.org/wiki/Design_of_experiments'>experiment design</a> and the page for <a href='https://en.wikipedia.org/wiki/University_of_Wisconsin%E2%80%93Madison'>UW-Madison</a>), but there are also links to lots of Wikipedia URLs that are not pages per se, in the sense that they are not about a particular topic.
For example, there's a link to this Category page: https://en.wikipedia.org/wiki/Category:Alumni_of_University_College_London.

Let's all take a few minutes to look at the links on the page and see if we can come up with some features we can check in the hyperlink URLs that will let us tell whether or not a given URL is indeed pointing to a Wikipedia page...

Once we've done that, let's implement all that in a function, `is_wiki_page` that takes a URL (i.e., a string) as its only argument and returns a Boolean encoding whether or not it is a Wikipedia page URL (as opposed to, e.g., an external link or a Wikipedia URL that is not the page for a particular topic/subject).

In [12]:
def is_wiki_page( url ):
    # CODE GOES HERE. Don't forget to remove pass.
    pass

Now, let's write a wrapper around this function that takes an `a` tag object and returns `True` if and only if it corresponds to a link to a Wikipedia page.

<b>Hint:</b> the actual URL of a hyperlink is stored in the `href` attribute. See <a href='https://beautiful-soup-4.readthedocs.io/en/latest/#attributes'>here</a> for documentation on retrieving attributes.

In [ ]:
def is_wiki_tag( tag ):
    # CODE GOES HERE. Don't forget to remove pass.
    pass

### Putting it all together, Part 1

We are now equipped to put our functions together into a single function which will, given a URL (which we will assume points to a valid Wikipedia page URL), return a list of the URLs of all the "neighbor" pages of the given that.
That is, a list of the URLs of all of the Wikipedia pages linked to by the given URL.
That means, given a starting URL `s`, we need to:

1. Retrieve the HTML from the URL at `s`
2. Parse the HTML document
3. Extract all of the `a` tags
4. Keep only the `a` tags that correspond to Wikipedia pages

Implement a function `get_neighbors` that takes a single string `url` (i.e., a URL) as its only argument, and returns a list of strings corresponding to the URLs of all Wikipedia pages linked to from the page at `url`.

In [ ]:
def get_neighhors( url ):
    # CODE GOES HERE. Don't forget to remove pass.
    pass

### Putting it all together, Part 2

Okay so now we know how to get all the Wikipedia pages linked to from a given page.
To get the $k$-hop neighborhood of a given Wiki page, it should suffice to just repeat this procedure $k$ times-- we get all the neighbors, then neighbors of neighbors (i.e., the 2-hop neighborhood), then neighbors of neighbors of neighbors, etc.

But if we want to actually keep track of the network structure that connects our Wiki pages, we have to be a bit more careful in our bookkeeping.

This means we'll have to keep track of which URLs we have visited and which ones link to which.
There are a lot of ways to do this, but for the sake of concreteness let's use the following scheme:

1. We will associate each Wikipedia page that we visit with an ID number. Our starting page will be `0` and we will just assign numbers sequentially from there.
2. We will maintain a pair of dictionaries for mapping IDs to URLs and URLs to IDs. Let's call these `id2url` and `url2id`, respectively.
3. For each page (i.e., each ID number), we will maintain <i>another</i> dictionary that maps each page (i.e., each vertex in our network) to a `set` object (recall that Python `set` objects are just dictionaries without keys) containing the IDs of all the pages it links to. Let's call this dictionary `id2neighbors`.

If we were being really serious about this, we would probably want to package all of these dictionaries up into a single object with methods for looking up neighbors, mapping IDs to URLs, etc.

Well, why not try and be professional? Define a class `WikiNetwork` that supports the following:

1. An initialization method that takes a single string (encoding a URL) as its only argument and initializes this as the starting vertex with ID 0.
2. A method `id2url` that takes a non-negative integer (representing a particular vertex) as its only argument and returns a string corresponding to the URL of that vertex.
3. A method `url2id` that takes a string representing a URL and returns the corresponding ID (i.e., reverse lookup of `id2url`).
4. A method `get_neighbors` that takes an ID and returns a set object containing the IDs of its neighbors in the network.

In [ ]:
class WikiNetwork:
    def __init__( self, url ):
        # CODE GOES HERE.
        pass
    
    def id2url( self, nodeid ):
        # CODE GOES HERE.
        pass
    
    def url2id( self, url ):
        # CODE GOES HERE.
        pass
    
    def get_neighbors( self, nodeid ):
        # CODE GOES HERE.
        pass

Now we have to put things together to get our $k$-hop neighborhood, one hop at a time.

Add a method to our class above called `hop`, which takes no arguments.
The function should take every vertex currently in the network, retrieve its URL, grab all the Wikipedia page links from the HTML stored at that URL, and add those pages as nodes in the network.

You may find it helpful to break this procedure down into sub-parts and perhaps write helper functions.

### Follow-up and improvements

#### Accounting for duplicate URLs

If you've spent any time clicking around on Wikipedia, you may have noticed that we have not accounted for one particular issue-- some Wikipedia pages have more than one URL!

For example, https://en.wikipedia.org/wiki/University_of_Wisconsin%E2%80%93Madison and https://en.wikipedia.org/wiki/University_of_Wisconsin both point to the same page.

How might we account for this? One possible option is to rely on the redirection error code. Try implementing that!

#### Plotting our network

It would be nice to be able to visualize our network, now that we've collected it.
The `igraph` library is a popular library for representing and visualizing network data.
Read the documentation <a href='https://igraph.org/python/'>here</a> and use `igraph` to visualize the 2-hop neighborhood around the Wikipedia page for George Box.

### Challenge project

Use our code above to write a program that plays <a href='https://en.wikipedia.org/wiki/Wikipedia:Wikirace'>Wikirace</a>.
The object of the game is to find the shortest path (via links) from one Wikipedia page to another.

<b>Hint:</b> the Wikipedia page on breadth-first search is a good resource. https://en.wikipedia.org/wiki/Breadth-first_search